In [1]:
import vectorbtpro as vbt
#from vectorbtpro import *
import os
import numpy as np
import talib
from numba import njit


In [1]:
pip list

Package                   Version
------------------------- --------------------
aiosignal                 1.3.1
annotated-types           0.7.0
anyio                     4.6.2.post1
arch                      7.1.0
argon2-cffi               23.1.0
argon2-cffi-bindings      21.2.0
arrow                     1.3.0
astropy                   6.1.4
astropy-iers-data         0.2024.10.21.0.33.21
asttokens                 2.4.1
async-lru                 2.0.4
attrs                     24.2.0
babel                     2.16.0
beautifulsoup4            4.12.3
bleach                    6.2.0
blinker                   1.8.2
blosc                     1.11.2
blosc2                    2.7.1
certifi                   2024.8.30
cffi                      1.17.1
charset-normalizer        3.4.0
clarabel                  0.9.0
click                     8.1.7
cloudpickle               3.1.0
colorama                  0.4.6
comm                      0.2.2
contourpy                 1.3.0
cvxpy                  

# CONFIGURAÇÃO


In [2]:
'''vbt.settings.execution.engine = 'serial'


# Configurações válidas de caching e chunking
vbt.settings.caching.update({
    'disable': False,
    'use_cached_accessors': True
})

vbt.settings.execution.update({
    'cache_chunks': True,
    'chunk_cache_dir': "cache_chunks",
    'release_chunk_cache': True
})
'''
vbt.settings.set_theme("dark")

# CARREGAR DADOS


In [5]:
# Carregando os dados de preços usando SerialEngine
DB_PATH = "../forex_market.duckdb"
symbol = "EURUSD"
data = vbt.DuckDBData.from_duckdb(symbol, start="2018-01-01", connection=DB_PATH)
print(data.close)
print(data.stats())

IOException: IO Error: Cannot open database "d:\caleb\caleb\python\mercado\mercado\ulysses\vectorbt_pro\..\forex_market.duckdb" in read-only mode: database does not exist

# RESAMPLE


In [149]:
time_frames = [1, 4, 24]
freqs = [f'{tf}h' for tf in time_frames]
h1_data = data.resample("1h")
h1_close = h1_data.close
h4_data = data.resample("4h")
h4_close = h4_data.close
h24_data = data.resample("24h")
h24_close = h24_data.close

print(h1_data.stats())
h24_data.plot().show()

Start Index            2007-01-01 20:00:00+00:00
End Index              2023-12-29 16:00:00+00:00
Total Duration                6205 days 21:00:00
Total Symbols                                  1
Null Counts: EURUSD                       220095
Name: agg_stats, dtype: object


# Indicador de tendência

In [150]:
high = h24_data.high.ffill().bfill()
low = h24_data.low.ffill().bfill()
close = h24_close.ffill().bfill()

In [151]:
def get_basic_bands(med_price, atr, multiplier):
    matr = multiplier * atr
    upper = med_price + matr
    lower = med_price - matr
    return upper, lower

In [153]:
@njit
def get_final_bands_nb(close, upper, lower):
    trend = np.full(close.shape, np.nan)
    dir_ = np.full(close.shape, 1)
    long = np.full(close.shape, np.nan)
    short = np.full(close.shape, np.nan)

    for i in range(1, close.shape[0]):
        if close[i] > upper[i - 1]:
            dir_[i] = 1
        elif close[i] < lower[i - 1]:
            dir_[i] = -1
        else:
            dir_[i] = dir_[i - 1]
            if dir_[i] > 0 and lower[i] < lower[i - 1]:
                lower[i] = lower[i - 1]
            if dir_[i] < 0 and upper[i] > upper[i - 1]:
                upper[i] = upper[i - 1]

        if dir_[i] > 0:
            trend[i] = long[i] = lower[i]
        else:
            trend[i] = short[i] = upper[i]
            
    return trend, dir_, long, short

In [154]:
def faster_supertrend_talib(high, low, close, period=7, multiplier=3):
    avg_price = talib.MEDPRICE(high, low)
    atr = talib.ATR(high, low, close, period)
    upper, lower = get_basic_bands(avg_price, atr, multiplier)
    return get_final_bands_nb(close, upper, lower)

In [155]:
# Executando o faster_supertrend_talib
trend, dir_, long, short = faster_supertrend_talib(
    high.values, 
    low.values, 
    close.values
)


valid_mask = np.isfinite(trend)
print("Valores válidos do trend:")
print(trend[valid_mask])
print(len(trend[valid_mask]))
print("\nDireção correspondente:")
print(dir_[valid_mask])
print(len(dir_[valid_mask]))
print("\nValores long válidos:")
print(long[np.isfinite(long)])
print(len(long[valid_mask]))
print("\nValores short válidos:")
print(short[np.isfinite(short)])
print(len(short[valid_mask]))

Valores válidos do trend:
[1.27197143 1.27197143 1.27197143 ... 1.09135173 1.09189434 1.09189434]
6200

Direção correspondente:
[1 1 1 ... 1 1 1]
6200

Valores long válidos:
[1.27197143 1.27197143 1.27197143 ... 1.09135173 1.09189434 1.09189434]
6200

Valores short válidos:
[1.36680653 1.36351274 1.36351274 ... 1.0922808  1.0922808  1.0922808 ]
6200


In [156]:
SuperTrend = vbt.IF(
    class_name='SuperTrend',
    short_name='st',
    input_names=['high', 'low', 'close'],
    param_names=['period', 'multiplier'],
    output_names=['supert', 'superd', 'superl', 'supers']
).with_apply_func(
    faster_supertrend_talib, 
    takes_1d=True,
    period=7, 
    multiplier=3
)

In [157]:
class SuperTrend(SuperTrend):
    def plot(self, 
             column=None, 
             close_kwargs=None,
             superl_kwargs=None,
             supers_kwargs=None,
             fig=None, 
             **layout_kwargs):
        close_kwargs = close_kwargs if close_kwargs else {}
        superl_kwargs = superl_kwargs if superl_kwargs else {}
        supers_kwargs = supers_kwargs if supers_kwargs else {}
        
        close = self.select_col_from_obj(self.close, column).rename('Close')
        supers = self.select_col_from_obj(self.supers, column).rename('Short')
        superl = self.select_col_from_obj(self.superl, column).rename('Long')
        
        fig = close.vbt.plot(fig=fig, **close_kwargs, **layout_kwargs)
        supers.vbt.plot(fig=fig, **supers_kwargs)
        superl.vbt.plot(fig=fig, **superl_kwargs)
        
        return fig

## Otimização

In [158]:
periods = np.arange(32, 65)
multipliers = np.arange(32, 65) / 10

In [159]:
st = SuperTrend.run(
    high, low, close, 
    period=periods, 
    multiplier=multipliers,
    param_product=True,
)
print(st.supert.dropna())

st_period                        32                                          \
st_multiplier                   3.2       3.3       3.4       3.5       3.6   
datetime                                                                      
2007-03-06 00:00:00+00:00  1.298413  1.297703  1.296992  1.296282  1.295571   
2007-03-07 00:00:00+00:00  1.298413  1.297703  1.296992  1.296282  1.295571   
2007-03-08 00:00:00+00:00  1.298413  1.297703  1.296992  1.296282  1.295571   
2007-03-09 00:00:00+00:00  1.298413  1.297703  1.296992  1.296282  1.295571   
2007-03-10 00:00:00+00:00  1.298413  1.297703  1.296992  1.296282  1.295571   
...                             ...       ...       ...       ...       ...   
2023-12-25 00:00:00+00:00  1.081362  1.080739  1.080116  1.079493  1.078870   
2023-12-26 00:00:00+00:00  1.082995  1.082380  1.081765  1.081150  1.080535   
2023-12-27 00:00:00+00:00  1.088023  1.087401  1.086778  1.086155  1.085532   
2023-12-28 00:00:00+00:00  1.089584  1.088954  1.088

In [160]:
# Escolha um período e multiplicador específico
periodos = [periods[0], periods[-1]]
multiplicadores = [multipliers[0], multipliers[-1]]

# Criando todas as combinações possíveis
combinacoes = [
    (periodos[0], multiplicadores[0]),  # (4, 2.0)
    (periodos[0], multiplicadores[-1]), # (4, 4.0)
    (periodos[-1], multiplicadores[0]), # (19, 2.0)
    (periodos[-1], multiplicadores[-1]) # (19, 4.0)
]

# Plotando cada combinação separadamente
for periodo, multiplicador in combinacoes:
    st.plot(
        column=(periodo, multiplicador),
        superl_kwargs=dict(trace_kwargs=dict(line_color='limegreen')),
        supers_kwargs=dict(trace_kwargs=dict(line_color='red')),
        title=f'SuperTrend - Período: {periodo}, Multiplicador: {multiplicador}'
    ).show()